In [ ]:
import os
os.chdir("/content/drive/MyDrive/DREAM")
!ls

 Data				       examine.ipynb	  FT_FIRST	      THIRD
 dictionary_73_11.pt		       finetune.ipynb	  hparams.ipynb       Trials
 dictionary.pt			       FIRST		  new_dictionary.pt   vectorizing.ipynb
 dream				       FOURTH		  SECOND
'Dream Olfactory Mixtures Plan.gdoc'   ft_examine.ipynb   submit.ipynb


In [ ]:
!rm -rf dream
!git clone https://github.com/laurahsisson/dream.git
import sys
sys.path.append("dream")

Cloning into 'dream'...
remote: Enumerating objects: 199, done.
remote: Counting objects: 100% (199/199), done.
remote: Compressing objects: 100% (143/143), done.
remote: Total 199 (delta 120), reused 131 (delta 55), pack-reused 0
Receiving objects: 100% (199/199), 358.81 KiB | 1.40 MiB/s, done.
Resolving deltas: 100% (120/120), done.


In [ ]:
!pip install torch-geometric
!pip install torch-scatter -f https://data.pyg.org/whl/torch-2.3.0+cu121.html
!pip install optuna

Looking in links: https://data.pyg.org/whl/torch-2.3.0+cu121.html


In [ ]:
import random
random.seed(42)

In [ ]:
import torch
import dream.tokenizer
tokenizer = dream.tokenizer.GraphTokenizer(torch.load("dictionary.pt"))

In [ ]:
# dictionary = {"x":tokenizer.x_tokenizer.unique_vector_tuples,"edge_attr":tokenizer.edge_attr_tokenizer.unique_vector_tuples}
# torch.save(dictionary,'dictionary.pt')

In [ ]:
import h5py
import numpy as np
import torch
import torch_geometric as tg
import numpy as np
import dream.data
import dream.dreamdata
import copy
from tqdm.notebook import tqdm

dream_data = dream.dreamdata.load_dream_h5('Data/train.h5')
dream_data[0]

100%|██████████| 500/500 [00:01<00:00, 254.50it/s]


{'graph1': BlendData(x=[273, 9], edge_index=[2, 514], edge_attr=[514, 3], blend_batch=[30], mol_batch=[273]),
 'graph2': BlendData(x=[251, 9], edge_index=[2, 472], edge_attr=[472, 3], blend_batch=[30], mol_batch=[251]),
 'y': tensor(0.5769),
 'dataset': 'Bushdid'}

In [ ]:
unique_datasets = set([d["dataset"] for d in dream_data])
unique_datasets

{'Bushdid', 'Ravia', 'Snitz 1', 'Snitz 2'}

In [ ]:
def tokenize_dream_entry(ds):
  ds = copy.copy(ds)
  ds["graph1"] = tokenizer.tokenize(ds["graph1"])
  ds["graph2"] = tokenizer.tokenize(ds["graph2"])
  return ds
dream_data_tokenized = [tokenize_dream_entry(ds) for ds in tqdm(dream_data)]
dream_data_tokenized[0]

  0%|          | 0/500 [00:00<?, ?it/s]

{'graph1': BlendData(x=[273], edge_index=[2, 514], edge_attr=[514], blend_batch=[30], mol_batch=[273]),
 'graph2': BlendData(x=[251], edge_index=[2, 472], edge_attr=[472], blend_batch=[30], mol_batch=[251]),
 'y': tensor(0.5769),
 'dataset': 'Bushdid'}

In [ ]:
for fold_dataset in unique_datasets:
  train_idx = [i for i in range(len(dream_data)) if dream_data[i]["dataset"] != fold_dataset]
  test_idx = [i for i in range(len(dream_data)) if dream_data[i]["dataset"] == fold_dataset]
  print(f"Fold Dataset = {fold_dataset}. Train Size = {len(train_idx)}. Test Size = {len(test_idx)}. Split = {len(test_idx)/len(train_idx):.2f}.")

Fold Dataset = Snitz 1. Train Size = 360. Test Size = 140. Split = 0.39.
Fold Dataset = Bushdid. Train Size = 266. Test Size = 234. Split = 0.88.
Fold Dataset = Snitz 2. Train Size = 419. Test Size = 81. Split = 0.19.
Fold Dataset = Ravia. Train Size = 455. Test Size = 45. Split = 0.10.


In [ ]:
import os
import json
import matplotlib.pyplot as plt
import numpy as np

min_reps = 0
min_auroc = 0

def load_config_files(directory_path):
    config_list = []

    # List all items in the given directory
    for item in tqdm(os.listdir(directory_path)):
        item_path = os.path.join(directory_path, item)

        # Check if the item is a directory
        if os.path.isdir(item_path):
            config_file_path = os.path.join(item_path, "config.json")

            # Check if the config.json file exists in the subdirectory
            if os.path.exists(config_file_path):
                with open(config_file_path, 'r') as f:
                    config = json.load(f)
                    if not "auroc" in config or np.isnan(config["auroc"]):
                      continue
                    if config["epochs"] <= min_reps:
                      continue
                    if config["auroc"] <= min_auroc:
                      continue
                    config["fname"] = item_path
                    config_list.append(config)

    return config_list

# Example usage
directory_path = "Trials/fourth_hparam_trials"
configs = load_config_files(directory_path)
sorted_configs = sorted(configs, key=lambda x: x['auroc'],reverse=True)

  0%|          | 0/358 [00:00<?, ?it/s]

In [ ]:
def parse_count(count):
  if isinstance(count,str):
    return int(count.replace(",", ""))
  return count

CUTOFF = .65
# MAX_SIZE = 1e5
MAX_SIZE = float('inf')

valid_configs = [cfg for cfg in sorted_configs if cfg["auroc"] >= CUTOFF and parse_count(cfg["count_parameters"]["total"])<MAX_SIZE]
valid_trials = [cfg["fname"] for cfg in valid_configs]
len(valid_trials), np.max([cfg["auroc"] for cfg in valid_configs])

(30, 0.7577065229415894)

In [ ]:
import dream.mpnn
import dream.encoder
import dream.olfactor

DEFAULT_VALUES = {"act_mode":"relu","aggr_mode":"sum"}

def make_defaults(config):
  config = copy.deepcopy(config)
  for k, v in DEFAULT_VALUES.items():
    if not k in config:
      config[k] = v

  if config["do_tokenize"]:
    config["graph_tokenizer"] = tokenizer
  else:
    config["graph_tokenizer"] = None

  config["mpnn_configs"] = [dream.mpnn.Config(*mpnn_cfg) for mpnn_cfg in config["mpnn_configs"]]

  return config

def load_trial_model(trial_path):
  with open(os.path.join(trial_path,"config.json")) as f:
    config = json.load(f)

  config = make_defaults(config)
  encoder = dream.encoder.Encoder(**config)
  olfactor = dream.olfactor.Olfactor(encoder,config["notes_dim"])
  olfactor.load_state_dict(torch.load(os.path.join(trial_path,"olfactor.pt")))

  return config, olfactor

In [ ]:
hyperparameter_trial_name = "second_finetune"

In [ ]:
import uuid
import time
import gc
import dream.cross
import dream.utils

def make_trial_id():
  TRIAL_ID_LENGTH = 6
  trial_id = str(uuid.uuid4())[:TRIAL_ID_LENGTH]
  return trial_id

def get_config(trial):
  layers = trial.suggest_int("cross_encoder_layers", 0, 2)
  if layers > 0:
    cross_encoder_dim = int(2**trial.suggest_int("cross_encoder_dim", 5, 11))
  else:
    cross_encoder_dim = -1

  do_warmup = True
  if do_warmup:
    warmup = trial.suggest_float("finetune_warmup", 0, 1)
  else:
    warmup = -1

  has_patience = trial.suggest_categorical("has_patience",[True,False]),
  if has_patience:
    finetune_patience = trial.suggest_int("finetune_patience",1,25)
  else:
    finetune_patience = 0

  return {
    # Base Model
    "pretrain_trial": trial.suggest_categorical("pretrain_trial",valid_trials),
    # Finetune Configurations
    "do_holdout": False,
    "finetune_epochs": 100,
    "has_patience": has_patience,
    "finetune_patience": finetune_patience,
    "do_encoder_diff": trial.suggest_categorical("do_encoder_diff",[True,False]),
    "representation_mode": trial.suggest_categorical("representation_mode",["embed","notes","both"]),
    "do_sigmoid": True,
    "cross_encoder_layers": layers,
    "cross_encoder_dim": cross_encoder_dim,
    "finetune_lr": trial.suggest_float("finetune_lr",1e-4,1e-2, log=True),
    "do_warmup": do_warmup,
    "finetune_warmup": warmup, # Probably have to retune every time we change epochs
    "finetune_weight_decay":trial.suggest_float("finetune_weight_decay", 0,1), # Probably have to retune every time we change epochs
    # Fixed parameters:
    # So only 128 fits
    "finetune_bsz": 64,
    "finetune_trial": make_trial_id()
  }

def make_dream_dataset(config,train_idx,test_idx):
  if config["do_tokenize"]:
    data = dream_data_tokenized
  else:
    data = dream_data
  return [data[i] for i in train_idx], [data[i] for i in test_idx]

def do_finetune_fold(config,olfactor,train_idx,test_idx,pbar,epochs):
  model = dream.cross.CrossEncoder(olfactor,**config)
  model.cuda()
  bsz = config["finetune_bsz"]
  data_train, data_test = make_dream_dataset(config,train_idx,test_idx)
  dream_train_loader = tg.loader.DataLoader(data_train, batch_size=bsz, shuffle=True)
  dream_test_loader = tg.loader.DataLoader(data_test, batch_size=bsz, shuffle=True)

  optimizer = torch.optim.AdamW(model.parameters(),lr=config["finetune_lr"],betas=config["betas"],weight_decay=config["finetune_weight_decay"])
  if config["do_warmup"]:
    scheduler = dream.utils.make_scheduler(optimizer, config["finetune_warmup"], epochs*len(dream_train_loader))
  else:
    scheduler = None

  def calc_loss(batch,reduction='mean'):
    graph1, graph2 = batch["graph1"], batch["graph2"]
    graph1.cuda()
    graph2.cuda()
    pred = model(graph1, graph2)
    # Leadboard is using RMSE
    return torch.nn.functional.mse_loss(pred,batch["y"].cuda(),reduction=reduction)

  def calc_test_rmse():
    tls = []
    with torch.no_grad():
      for tbatch in dream_test_loader:
        with torch.cuda.amp.autocast():
          tls.append(calc_loss(tbatch,reduction='sum').cpu().detach().numpy())
    return np.sqrt(np.sum(tls)/len(data_test))

  train_losses = []
  test_losses = []
  best_loss = float('inf')
  patience = 0

  for epoch in range(epochs):
    btls = []
    model.train()
    for batch in dream_train_loader:
      loss = calc_loss(batch)

      loss.backward()
      optimizer.step()
      if scheduler:
        scheduler.step()

      optimizer.zero_grad()
      btls.append(loss.cpu().detach())

    model.eval()
    pbar.update(1)
    tl = calc_test_rmse()
    test_losses.append(tl)
    train_losses.append(np.sqrt(np.mean(btls)))

    if tl <= best_loss:
      best_loss = tl
      patience = 0
    else:
      patience += 1
      if patience >= config["finetune_patience"]:
        # Skip ahead
        pbar.update((epochs-epoch)-1)
        break


  return test_losses[-1].item()

def do_finetune(trial,config,olfactor):
  print(f"Trial ID = {config['finetune_trial']}. Model size = {parse_count(config['count_parameters']['total']):,}",config,sep="\n")
  losses = []
  folds = len(unique_datasets)

  steps = folds * config["finetune_epochs"]
  with tqdm(total=steps,smoothing=0) as pbar:
    # We will do k-fold validation with each dataset as the test set
    # to evalaute how well the model transfers to unseen data
    for i,fold_dataset in enumerate(unique_datasets):
      train_idx = [i for i in range(len(dream_data)) if dream_data[i]["dataset"] != fold_dataset]
      test_idx = [i for i in range(len(dream_data)) if dream_data[i]["dataset"] == fold_dataset]
      fold_best_loss = do_finetune_fold(config,olfactor,train_idx,test_idx,pbar,config["finetune_epochs"])
      losses.append(fold_best_loss)

      trial.report(fold_best_loss, i)
      if trial.should_prune():
        raise optuna.TrialPruned()

  print([f"{ds} = {loss:.3f}" for (ds,loss) in zip(unique_datasets,losses)])
  # Report results on worst dataset
  return np.median(losses).item(), losses

def train_model(trial,display_model=False):
  print()
  gc.collect()
  torch.cuda.empty_cache()

  start = time.perf_counter()
  config = get_config(trial)
  pretrain_config, olfactor = load_trial_model(config["pretrain_trial"])
  config = config | pretrain_config

  rmse, fold_rmses = do_finetune(trial,config,olfactor)

  path = os.path.join("Trials",hyperparameter_trial_name,config["finetune_trial"])
  os.makedirs(path,exist_ok=True)
  with open(os.path.join(path,"config.json"),"w") as f:
    config["rmse"] = rmse
    config["fold_rmses"] = fold_rmses
    config["time"] = time.perf_counter() - start
    del config["graph_tokenizer"]
    json.dump(config,f)

  return rmse

####
import optuna

num_trials = 256

# study = optuna.create_study(
#     direction="minimize",
#     sampler=optuna.samplers.QMCSampler(qmc_type="halton",scramble=True,warn_independent_sampling=False),
#     pruner=optuna.pruners.NopPruner())

study = optuna.create_study(
    direction="minimize",
    sampler= optuna.samplers.TPESampler(seed=42),
    pruner=optuna.pruners.HyperbandPruner())
study.optimize(train_model, n_trials=num_trials, catch=(AssertionError,))

print("DONE")
print("CONFIG:", study.best_trial.params)
print("METRICS:", study.best_trial.values)

[I 2024-07-30 03:04:15,914] A new study created in memory with name: no-name-cd0c96ec-0eb1-40d4-83c0-a19ef5cc4ebc



Trial ID = 09fafe. Model size = 335,792
{'pretrain_trial': 'Trials/fourth_hparam_trials/4e3047', 'do_holdout': False, 'finetune_epochs': 100, 'has_patience': (True,), 'finetune_patience': 4, 'do_encoder_diff': True, 'representation_mode': 'embed', 'do_sigmoid': True, 'cross_encoder_layers': 1, 'cross_encoder_dim': 2048, 'finetune_lr': 0.0009780337016659412, 'do_warmup': True, 'finetune_warmup': 0.7319939418114051, 'finetune_weight_decay': 0.034388521115218396, 'finetune_bsz': 64, 'finetune_trial': '09fafe', 'epochs': 5, 'train_size': 213160, 'test_size': 53290, 'do_tokenize': False, 'do_edge_update': True, 'do_two_stage': False, 'embedding_dim_x': 16, 'embedding_dim_edge_attr': 8, 'dropout': 0.2536773300674443, 'num_sabs': 5, 'mpnn_configs': [Config(node_out_feats=64, edge_hidden_feats=16, num_step_message_passing=5)], 'heads': 8, 'aggr_mode': 'max', 'act_mode': 'silu', 'pretrain_lr': 0.00014718955390563673, 'warmup': 0.037769954406489836, 'weight_decay': 0.05, 'bsz': 2048, 'betas': [

  0%|          | 0/400 [00:00<?, ?it/s]

[I 2024-07-30 03:05:37,906] Trial 0 finished with value: 0.15273141703550236 and parameters: {'cross_encoder_layers': 1, 'cross_encoder_dim': 11, 'finetune_warmup': 0.7319939418114051, 'has_patience': True, 'finetune_patience': 4, 'pretrain_trial': 'Trials/fourth_hparam_trials/4e3047', 'do_encoder_diff': True, 'representation_mode': 'embed', 'finetune_lr': 0.0009780337016659412, 'finetune_weight_decay': 0.034388521115218396}. Best is trial 0 with value: 0.15273141703550236.


['Snitz 1 = 0.170', 'Bushdid = 0.176', 'Snitz 2 = 0.127', 'Ravia = 0.135']

Trial ID = 6c2485. Model size = 930,704
{'pretrain_trial': 'Trials/fourth_hparam_trials/aa718a', 'do_holdout': False, 'finetune_epochs': 100, 'has_patience': (False,), 'finetune_patience': 14, 'do_encoder_diff': False, 'representation_mode': 'embed', 'do_sigmoid': True, 'cross_encoder_layers': 2, 'cross_encoder_dim': 64, 'finetune_lr': 0.0004187594718900631, 'do_warmup': True, 'finetune_warmup': 0.662522284353982, 'finetune_weight_decay': 0.32518332202674705, 'finetune_bsz': 64, 'finetune_trial': '6c2485', 'epochs': 5, 'train_size': 213160, 'test_size': 53290, 'do_tokenize': False, 'do_edge_update': False, 'do_two_stage': True, 'embedding_dim_x': 8, 'embedding_dim_edge_attr': 32, 'dropout': 0.09386757977017922, 'num_sabs': 7, 'mpnn_configs': [Config(node_out_feats=64, edge_hidden_feats=64, num_step_message_passing=3)], 'heads': 2, 'aggr_mode': 'mean', 'act_mode': 'silu', 'pretrain_lr': 0.007957452852563008, 'wa

...

[I 2024-07-30 11:01:06,472] Trial 254 pruned. 



Trial ID = d89e40. Model size = 19,048
{'pretrain_trial': 'Trials/fourth_hparam_trials/0c6db2', 'do_holdout': False, 'finetune_epochs': 100, 'has_patience': (False,), 'finetune_patience': 17, 'do_encoder_diff': True, 'representation_mode': 'both', 'do_sigmoid': True, 'cross_encoder_layers': 2, 'cross_encoder_dim': 256, 'finetune_lr': 0.00043901908427865395, 'do_warmup': True, 'finetune_warmup': 0.27616510028419566, 'finetune_weight_decay': 0.5887506095504251, 'finetune_bsz': 64, 'finetune_trial': 'd89e40', 'epochs': 50, 'train_size': 213160, 'test_size': 53290, 'num_mpnns': 2, 'do_tokenize': False, 'do_edge_update': True, 'do_two_stage': True, 'embedding_dim_x': 32, 'embedding_dim_edge_attr': 64, 'dropout': 0.04354475342824933, 'num_sabs': 1, 'mpnn_configs': [Config(node_out_feats=8, edge_hidden_feats=8, num_step_message_passing=1), Config(node_out_feats=16, edge_hidden_feats=16, num_step_message_passing=1)], 'heads': 16, 'aggr_mode': 'mean', 'act_mode': 'relu', 'pretrain_lr': 0.00470

  0%|          | 0/400 [00:00<?, ?it/s]

[I 2024-07-30 11:02:47,819] Trial 255 pruned. 


DONE
CONFIG: {'cross_encoder_layers': 2, 'cross_encoder_dim': 8, 'finetune_warmup': 0.5294927310097122, 'has_patience': True, 'finetune_patience': 17, 'pretrain_trial': 'Trials/fourth_hparam_trials/0c6db2', 'do_encoder_diff': True, 'representation_mode': 'notes', 'finetune_lr': 0.0028405774150850197, 'finetune_weight_decay': 0.5978205816681027}
METRICS: [0.11705612898293619]


In [ ]:
from google.colab import runtime
runtime.unassign()